# Wildfire Proximity Computation Example
This Jupyter notebook contains example code that illustrate how to perform some basic geodetic computations related to the Wildfire course project. The notebook is structured as a set of examples that illustrate something about the the data schema or illustrate a way to compute specific values. This notebook is not a tutorial on performing geodetic computations, but illustrates a number of key concepts. This notebook should provide enough information to complete the Wildfire assignment.

The complete [Wildfire dataset](https://www.sciencebase.gov/catalog/item/61aa537dd34eb622f699df81) can be retrieved from a US government repository. I have noticed that the repository is sometimes "down" and does not respond. It probably makes sense to get the dataset as soon as possible.

This notebook has dependencies on [Pyproj](https://pyproj4.github.io/pyproj/stable/index.html), the [geojson](https://pypi.org/project/geojson/) module and on the wildfire user module. Pyproj and geojson can be installed via pip. The wildfire user module should be downloaded from the course website, unzipped, and moved into the folder pointed to by your PYTHONPATH system variable.

### License
This code example was developed by Dr. David W. McDonald for use in DATA 512, a course in the UW MS Data Science degree program. This code is provided under the [Creative Commons](https://creativecommons.org) [CC-BY license](https://creativecommons.org/licenses/by/4.0/). Revision 1.1 - August 16, 2024

### Preliminaries
First we start with some imports and some constant definitions.

In [1]:
import pandas as pd
import os, json, time
from pyproj import Transformer, Geod
from Reader import Reader as WFReader

In [2]:
TALAHASSEE_COORDS = [30.46, -84.25]  
SRCH_RADIUS = 650 

EST_NUM_FIRES = 136000

In [3]:
wildfire_json = 'USGS_Wildland_Fire_Combined_Dataset.json'
wildfire_data_directory = r'C:\Users\clark.roll\python coding\code_personal\Data512_ProjectDataset'
json_file_path = os.path.join(wildfire_data_directory, wildfire_json)

In [4]:
def load_wildfire_features(json_file_path, max_features=EST_NUM_FIRES):
    """
    Load features from a JSON file using the wildfire Reader object and show progress.
    
    Parameters:
    - json_file_path (str): Path to the JSON file containing wildfire data.
    - max_features (int): Maximum number of features to load.
    
    Returns:
    - feature_list (list): List of loaded features.
    """
    print(f"Attempting to open '{json_file_path}' with wildfire.Reader() object")
    
    # Initialize Reader
    wfreader = WFReader(json_file_path)
    print()
    
    # Print header information
    header_dict = wfreader.header()
    print("The header contains the following keys:")
    print(list(header_dict.keys()))
    print("Header Dictionary:")
    print(json.dumps(header_dict, indent=4))
    print()
    
    # Initialize feature list and counters
    feature_list = []
    feature_count = 0
    
    # Ensure reader is at the start of the file
    wfreader.rewind()
    
    # Load features and track progress
    feature = wfreader.next()
    while feature:
        feature_list.append(feature)
        feature_count += 1
        
        # Print progress every 100 features
        if feature_count % 100 == 0:
            print(f"Loaded {feature_count} features")
        
        # Stop if maximum features reached
        if feature_count >= max_features:
            break
        
        # Load the next feature
        feature = wfreader.next()
    
    # Final output of feature count
    print(f"Loaded a total of {feature_count} features")
    print(f"Variable 'feature_list' contains {len(feature_list)} features")
    
    return feature_list

In [5]:
wildfire_data =  load_wildfire_features(json_file_path, max_features=EST_NUM_FIRES)

Attempting to open 'C:\Users\clark.roll\python coding\code_personal\Data512_ProjectDataset\USGS_Wildland_Fire_Combined_Dataset.json' with wildfire.Reader() object

The header contains the following keys:
['displayFieldName', 'fieldAliases', 'geometryType', 'spatialReference', 'fields']
Header Dictionary:
{
    "displayFieldName": "",
    "fieldAliases": {
        "OBJECTID": "OBJECTID",
        "USGS_Assigned_ID": "USGS Assigned ID",
        "Assigned_Fire_Type": "Assigned Fire Type",
        "Fire_Year": "Fire Year",
        "Fire_Polygon_Tier": "Fire Polygon Tier",
        "Fire_Attribute_Tiers": "Fire Attribute Tiers",
        "GIS_Acres": "GIS_Acres",
        "GIS_Hectares": "GIS_Hectares",
        "Source_Datasets": "Source Datasets",
        "Listed_Fire_Types": "Listed Fire Types",
        "Listed_Fire_Names": "Listed Fire Names",
        "Listed_Fire_Codes": "Listed Fire Codes",
        "Listed_Fire_IDs": "Listed Fire IDs",
        "Listed_Fire_IRWIN_IDs": "Listed Fire IRWIN ID

In [6]:
# Initialize the geodesic model with WGS84 ellipsoid
geodesic_calculator = Geod(ellps='WGS84')

# Transformer to convert ESRI:102008 coordinates to EPSG:4326 (WGS84)
to_epsg4326 = Transformer.from_crs("ESRI:102008", "EPSG:4326", always_xy=True)

# Function to convert ring coordinates to EPSG:4326
def convert_ring_to_epsg4326_B(ring_data=None):
    converted_ring = []
    for coord in ring_data:
        lon, lat = to_epsg4326.transform(coord[0], coord[1])
        converted_ring.append((lat, lon))
    return converted_ring

def convert_ring_to_epsg4326(ring_data):
    converted_ring = []
    to_epsg4326 = Transformer.from_crs("ESRI:102008", "EPSG:4326")

    for coord in ring_data:
        # Ensure coordinate data is present and structured as expected
        if isinstance(coord, list) and len(coord) >= 2:
            try:
                lon, lat = to_epsg4326.transform(coord[0], coord[1])
                converted_ring.append((lat, lon))
            except Exception as e:
                print(f"Error transforming coordinates {coord}: {e}")
        else:
            print(f"Skipping invalid coordinate data: {coord}")

    return converted_ring
# Function to get the shortest distance from a place to a fire perimeter
def shortest_distance_from_place_to_fire_perimeter(place=None, ring_data=None):
    transformed_ring = convert_ring_to_epsg4326(ring_data)
    closest_distance = float('inf')
    closest_point = None

    for perimeter_point in transformed_ring:
        dist = geodesic_calculator.inv(
            place[1], place[0], perimeter_point[1], perimeter_point[0]
        )[2]
        distance_in_miles = dist * 0.00062137

        if distance_in_miles < closest_distance:
            closest_distance = distance_in_miles
            closest_point = perimeter_point

    return closest_distance, closest_point

# Function to find all fires within a specific range of a given location
def find_fires_within_range(location, max_distance_miles, feature_list):
    fires_within_range = []
    total_features = len(feature_list)

    for feature_index, fire_feature in enumerate(feature_list):
        # Progress printout every 100 features
        if feature_index % 100 == 0:
            print(f"Processing feature {feature_index + 1} of {total_features}...")

        fire_attributes = fire_feature.get('attributes', {})
        fire_geometry = fire_feature.get('geometry', {})

        # Skip features without the necessary geometry data
        if 'rings' in fire_geometry:
            ring_data = fire_geometry['rings'][0]
        elif 'curveRings' in fire_geometry:
            ring_data = fire_geometry['curveRings'][0]
        else:
            continue

        # Calculate the shortest distance to the fire perimeter
        closest_distance, closest_point = shortest_distance_from_place_to_fire_perimeter(location, ring_data)

        # Debugging: Print the closest distance and verify it’s below the threshold
        print(f"Feature {feature_index + 1}: Closest distance to perimeter = {closest_distance:.2f} miles")

        # Check if the distance is within the specified maximum range
        if closest_distance <= max_distance_miles:
            fires_within_range.append({
                'fire_name': fire_attributes.get('Listed_Fire_Names', 'Unknown Fire').split(',')[0],
                'fire_year': fire_attributes.get('Fire_Year', 'Unknown Year'),
                'fire_size_acres': fire_attributes.get('GIS_Acres', 0),
                'closest_distance_miles': closest_distance,
                'perimeter_points_count': len(ring_data),
                'closest_point': closest_point
            })

    # Debugging: If no fires are within range, print a message
    if not fires_within_range:
        print(f"No fires found within {max_distance_miles} miles of location {location}.")

    print(f"Finished processing {total_features} features.")
    return fires_within_range

In [7]:
num_subsets = 4
total_entries = len(wildfire_data)
subset_size = total_entries // num_subsets  # Approximate size of each subset
subsets = []

for subset_index in range(num_subsets):
    start_index = subset_index * subset_size
    end_index = start_index + subset_size

    # Adjust the last subset to include any remaining entries
    if subset_index == num_subsets - 1:
        subsets.append(wildfire_data[start_index:])
    else:
        subsets.append(wildfire_data[start_index:end_index])

# Assign each subset to a variable for further use
wildfire_subset1, wildfire_subset2, wildfire_subset3, wildfire_subset4 = subsets

In [8]:
sub4_fires_in_range = find_fires_within_range(TALAHASSEE_COORDS,
                                              SRCH_RADIUS,
                                              wildfire_subset4)

Processing feature 1 of 33766...
Feature 1: Closest distance to perimeter = 8464.60 miles
Feature 2: Closest distance to perimeter = inf miles
Feature 3: Closest distance to perimeter = 8518.67 miles
Feature 4: Closest distance to perimeter = 8478.04 miles
Feature 5: Closest distance to perimeter = inf miles
Feature 6: Closest distance to perimeter = 8499.41 miles
Feature 7: Closest distance to perimeter = inf miles
Feature 8: Closest distance to perimeter = 8408.15 miles
Feature 9: Closest distance to perimeter = inf miles
Feature 10: Closest distance to perimeter = 8416.07 miles
Feature 11: Closest distance to perimeter = 8455.25 miles
Feature 12: Closest distance to perimeter = 8514.98 miles
Feature 13: Closest distance to perimeter = 8518.34 miles
Feature 14: Closest distance to perimeter = inf miles
Feature 15: Closest distance to perimeter = 8466.96 miles
Feature 16: Closest distance to perimeter = inf miles
Feature 17: Closest distance to perimeter = 8399.26 miles
Feature 18: Cl

KeyboardInterrupt: 

In [14]:
sub1_fires_in_range = find_fires_within_range(TALAHASSEE_COORDS,
                                              SRCH_RADIUS,
                                              wildfire_subset1)

Processing feature 1 of 33765...
Feature 1: Closest distance to perimeter = 2367.72 miles
Feature 2: Closest distance to perimeter = 2367.20 miles
Feature 3: Closest distance to perimeter = 2369.40 miles
Feature 4: Closest distance to perimeter = 1998.57 miles
Feature 5: Closest distance to perimeter = 1883.79 miles
Feature 6: Closest distance to perimeter = 1983.15 miles
Feature 7: Closest distance to perimeter = 1969.65 miles
Feature 8: Closest distance to perimeter = 1962.05 miles
Feature 9: Closest distance to perimeter = 1309.25 miles
Feature 10: Closest distance to perimeter = 1443.03 miles
Feature 11: Closest distance to perimeter = 1446.34 miles
Feature 12: Closest distance to perimeter = 1433.80 miles
Feature 13: Closest distance to perimeter = 1433.44 miles
Feature 14: Closest distance to perimeter = 1736.76 miles
Feature 15: Closest distance to perimeter = 1963.84 miles
Feature 16: Closest distance to perimeter = 1802.29 miles
Feature 17: Closest distance to perimeter = 1831

In [15]:
sub2_fires_in_range = find_fires_within_range(TALAHASSEE_COORDS,
                                         SRCH_RADIUS,
                                         wildfire_subset2)

Processing feature 1 of 33765...
Feature 1: Closest distance to perimeter = 369.19 miles
Feature 2: Closest distance to perimeter = 366.63 miles
Feature 3: Closest distance to perimeter = 583.56 miles
Feature 4: Closest distance to perimeter = 1389.28 miles
Feature 5: Closest distance to perimeter = 786.37 miles
Feature 6: Closest distance to perimeter = 622.46 miles
Feature 7: Closest distance to perimeter = 2246.91 miles
Feature 8: Closest distance to perimeter = 2237.45 miles
Feature 9: Closest distance to perimeter = 2232.55 miles
Feature 10: Closest distance to perimeter = 2232.31 miles
Feature 11: Closest distance to perimeter = 2061.01 miles
Feature 12: Closest distance to perimeter = 2065.62 miles
Feature 13: Closest distance to perimeter = 2069.24 miles
Feature 14: Closest distance to perimeter = 2072.07 miles
Feature 15: Closest distance to perimeter = 2022.22 miles
Feature 16: Closest distance to perimeter = 2073.11 miles
Feature 17: Closest distance to perimeter = 2073.79 m

In [17]:
sub3_fires_in_range = find_fires_within_range(TALAHASSEE_COORDS,
                                         SRCH_RADIUS,
                                         wildfire_subset3)

Processing feature 1 of 33765...
Feature 1: Closest distance to perimeter = 3816.09 miles
Feature 2: Closest distance to perimeter = 301.02 miles
Feature 3: Closest distance to perimeter = 1925.99 miles
Feature 4: Closest distance to perimeter = 1476.24 miles
Feature 5: Closest distance to perimeter = 272.69 miles
Feature 6: Closest distance to perimeter = 244.63 miles
Feature 7: Closest distance to perimeter = 1932.88 miles
Feature 8: Closest distance to perimeter = 1575.15 miles
Feature 9: Closest distance to perimeter = 1499.54 miles
Feature 10: Closest distance to perimeter = 1547.11 miles
Feature 11: Closest distance to perimeter = 1547.68 miles
Feature 12: Closest distance to perimeter = 1985.45 miles
Feature 13: Closest distance to perimeter = 1634.06 miles
Feature 14: Closest distance to perimeter = 1956.58 miles
Feature 15: Closest distance to perimeter = 57.06 miles
Feature 16: Closest distance to perimeter = 1548.25 miles
Feature 17: Closest distance to perimeter = 1639.05 m

In [23]:
combined_fires_in_range = sub1_fires_in_range + sub2_fires_in_range + sub3_fires_in_range

# Step 2: Convert the combined list to a DataFrame
fires_df = pd.DataFrame(combined_fires_in_range)

In [24]:
fires_df

fire_name  fire_year  fire_size_acres  \
0        Laurel Branch (14)       1920       498.893971   
1       Spruce Mountain (2)       1923       856.766473   
2         Goshen Ridge (16)       1925      5870.435330   
3           Balsam/Cat (12)       1925      8709.390470   
4                  Dome (2)       1925      2272.104218   
...                     ...        ...              ...   
16270           UNNAMED (2)       2007      2805.776635   
16271           UNNAMED (1)       2007      1456.958562   
16272           UNNAMED (1)       2007      1455.264777   
16273       UNIT C 20 A (1)       2007      2733.505627   
16274  2-1-2 QUADRANGLE (1)       2007      1430.313479   

       closest_distance_miles  perimeter_points_count  \
0                  360.637607                      60   
1                  360.106655                     321   
2                  356.583082                      32   
3                  362.257390                     919   
4                  352.066103                     465   
...                       ...                     ...   
16270              294.840164                     132   
16271              641.746472                     187   
16272              255.511460                     105   
16273              249.716892                     224   
16274              612.702906                      91   

                                  closest_point  
0       (35.66241165344432, -83.57646729414687)  
1      (35.604207223018356, -83.15912115839201)  
2       (35.600642397355045, -83.5491645136673)  
3       (35.64084835097713, -83.19262713148186)  
4       (35.53126356302195, -83.51529959408765)  
...                                         ...  
16270   (26.98962341616984, -81.40485391543062)  
16271  (34.640226769764475, -94.08441758844896)  
16272  (27.222521468771905, -82.19134625370367)  
16273   (28.56023313526123, -80.71916427371698)  
16274   (35.85291251585325, -75.83723231281947)  

[16275 rows x 6 columns]

In [25]:
# Step 3: Save the DataFrame to a CSV file (or another format if preferred)
fires_df.to_csv("combined_fires_in_range.csv", index=False)

In [10]:
def convert_ring_to_epsg4326(ring_data):
    converted_ring = []
    to_epsg4326 = Transformer.from_crs("ESRI:102008", "EPSG:4326")

    for coord in ring_data:
        # Ensure coordinate data is present and structured as expected
        if isinstance(coord, list) and len(coord) >= 2:
            try:
                lon, lat = to_epsg4326.transform(coord[0], coord[1])
                converted_ring.append((lat, lon))
            except Exception as e:
                print(f"Error transforming coordinates {coord}: {e}")
        else:
            print(f"Skipping invalid coordinate data: {coord}")

    return converted_ring

In [11]:
sub4_fires_in_range = find_fires_within_range(TALAHASSEE_COORDS,
                                         SRCH_RADIUS,
                                         wildfire_subset4)

Processing feature 1 of 33766...
Feature 1: Closest distance to perimeter = 8464.60 miles
Feature 2: Closest distance to perimeter = inf miles
Feature 3: Closest distance to perimeter = 8518.67 miles
Feature 4: Closest distance to perimeter = 8478.04 miles
Feature 5: Closest distance to perimeter = inf miles
Feature 6: Closest distance to perimeter = 8499.41 miles
Feature 7: Closest distance to perimeter = inf miles
Feature 8: Closest distance to perimeter = 8408.15 miles
Feature 9: Closest distance to perimeter = inf miles
Feature 10: Closest distance to perimeter = 8416.07 miles
Feature 11: Closest distance to perimeter = 8455.25 miles
Feature 12: Closest distance to perimeter = 8514.98 miles
Feature 13: Closest distance to perimeter = 8518.34 miles
Feature 14: Closest distance to perimeter = inf miles
Feature 15: Closest distance to perimeter = 8466.96 miles
Feature 16: Closest distance to perimeter = inf miles
Feature 17: Closest distance to perimeter = 8399.26 miles
Feature 18: Cl

KeyboardInterrupt: 

In [21]:
sub5fires_in_range = find_fires_within_range(TALAHASSEE_COORDS,
                                         SRCH_RADIUS,
                                         wildfire_subset3)

Processing feature 1 of 33765...
Feature 1: Closest distance to perimeter = inf miles
Feature 2: Closest distance to perimeter = 8330.52 miles
Feature 3: Closest distance to perimeter = inf miles
Feature 4: Closest distance to perimeter = inf miles
Feature 5: Closest distance to perimeter = 8348.19 miles
Feature 6: Closest distance to perimeter = 8531.32 miles
Feature 7: Closest distance to perimeter = inf miles
Feature 8: Closest distance to perimeter = inf miles
Feature 9: Closest distance to perimeter = inf miles
Feature 10: Closest distance to perimeter = inf miles
Feature 11: Closest distance to perimeter = inf miles
Feature 12: Closest distance to perimeter = inf miles
Feature 13: Closest distance to perimeter = inf miles
Feature 14: Closest distance to perimeter = inf miles
Feature 15: Closest distance to perimeter = 8444.03 miles
Feature 16: Closest distance to perimeter = inf miles
Feature 17: Closest distance to perimeter = inf miles
Feature 18: Closest distance to perimeter 

KeyboardInterrupt: 

## Example 2. Load the wildfire data using the wildfire Reader object

In the following cells we provide small code snippets that do the following:
- Create a wildfire Reader() object and use it to open the sample data file. Once, opened, we have access to the header information so we print that to show the structure of that data.
- Use the Reader() object and the next() method to read a set of wildfire features. The small sample file should have 15 of them. 
- Print one example feature showing the dictionary data structure of a feature.
- Access the geometry of one specific feature to get the 'ring' boundary of that specific fire - which is a list of geodetic coordinates.

Note that some of the output cells are quite long. Once you understand what they are illustrating you might want to collapse them or comment out the print statements that generate the output.

Another note regarding terminology. In the GeoJSON standard, something that is to be represented geographically is generically called a 'feature'. In the case of the wildfire dataset every 'feature' is a wildfire. These terms are used somewhat interchangably below.


In [6]:
#
#    This bit of code opens a new wildfire reader, gets the header information and prints it to the screen
#
print(f"Attempting to open '{SAMPLE_DATA_FILENAME}' with wildfire.Reader() object")
wfreader = WFReader(SAMPLE_DATA_FILENAME)
print()
#
#    Now print the header - it contains some useful information
#
header_dict = wfreader.header()
header_keys = list(header_dict.keys())
print("The header has the following keys:")
print(gj_keys)
print()
print("Header Dictionary")
print(json.dumps(header_dict,indent=4))

Attempting to open '/Users/dwmc/Development/working3/wildfire/Wildfire_short_sample_2024.json' with wildfire.Reader() object

The header has the following keys:
['displayFieldName', 'fieldAliases', 'geometryType', 'spatialReference', 'fields', 'features']

Header Dictionary
{
    "displayFieldName": "",
    "fieldAliases": {
        "OBJECTID": "OBJECTID",
        "USGS_Assigned_ID": "USGS Assigned ID",
        "Assigned_Fire_Type": "Assigned Fire Type",
        "Fire_Year": "Fire Year",
        "Fire_Polygon_Tier": "Fire Polygon Tier",
        "Fire_Attribute_Tiers": "Fire Attribute Tiers",
        "GIS_Acres": "GIS_Acres",
        "GIS_Hectares": "GIS_Hectares",
        "Source_Datasets": "Source Datasets",
        "Listed_Fire_Types": "Listed Fire Types",
        "Listed_Fire_Names": "Listed Fire Names",
        "Listed_Fire_Codes": "Listed Fire Codes",
        "Listed_Fire_IDs": "Listed Fire IDs",
        "Listed_Fire_IRWIN_IDs": "Listed Fire IRWIN IDs",
        "Listed_Fire_Dates"

In [7]:
#
#    This sample code will load the whole sample (extracted data) file, or a small amount of the complete dataset.
#
MAX_FEATURE_LOAD = 100
feature_list = list()
feature_count = 0
# A rewind() on the reader object makes sure we're at the start of the feature list
# This way, we can execute this cell multiple times and get the same result 
wfreader.rewind()
# Now, read through each of the features, saving them as dictionaries into a list
feature = wfreader.next()
while feature:
    feature_list.append(feature)
    feature_count += 1
    # if we're loading a lot of features, print progress
    if (feature_count % 100) == 0:
        print(f"Loaded {feature_count} features")
    # loaded the max we're allowed then break
    if feature_count >= MAX_FEATURE_LOAD:
        break
    feature = wfreader.next()
#
#    Print the number of items (features) we think we loaded
print(f"Loaded a total of {feature_count} features")
#
#    Just a validation check - did all the items we loaded get into the list?
print(f"Variable 'feature_list' contains {len(feature_list)} features")




Loaded a total of 15 features
Variable 'feature_list' contains 15 features


In [8]:
#
#    The 'feature_list' variable was created when we read the sample file in a code cell above
#    Now, we're just going to look at one single feature - see what is in there
#
SLOT = 0
wf_feature = feature_list[SLOT]

# Print everyting in this dictionary (i.e., wf_feature) - it's long
print(f"The wildfire feature from slot '{SLOT}' of the loaded 'feature_list'")
print(json.dumps(wf_feature, indent=4))


The wildfire feature from slot '0' of the loaded 'feature_list'
{
    "attributes": {
        "OBJECTID": 4956,
        "USGS_Assigned_ID": 4956,
        "Assigned_Fire_Type": "Wildfire",
        "Fire_Year": 1932,
        "Fire_Polygon_Tier": 1,
        "Fire_Attribute_Tiers": "1 (1), 3 (3)",
        "GIS_Acres": 219999.23754748085,
        "GIS_Hectares": 89030.53273921262,
        "Source_Datasets": "Comb_National_NIFC_Interagency_Fire_Perimeter_History (1), Comb_National_USFS_Final_Fire_Perimeter (1), Comb_National_WFDSS_Interagency_Fire_Perimeter_History (1), Comb_State_California_Wildfire_Polygons (1)",
        "Listed_Fire_Types": "Wildfire (3), Likely Wildfire (1)",
        "Listed_Fire_Names": "MATILIJA (4)",
        "Listed_Fire_Codes": "No code provided (4)",
        "Listed_Fire_IDs": "0 (3)",
        "Listed_Fire_IRWIN_IDs": "",
        "Listed_Fire_Dates": "Listed Wildfire Discovery Date(s): 1932-09-07 (2) | Listed Other Fire Date(s): 1899-12-30 - REVDATE field (1), 1932-